# Robert Smith - Python WOW Project

# Dial-A-Newscast (929-209-6415)

As a radio reporter, my passion is audio and I wanted to explore the ways that python could be used to distribute audio files.

This project created a telephone number that you can call at any time of day to get the latest, updated NPR newscast. To accomplish this, I needed the following skills:

--Web-scraping to find the latest newscast

--File manipulation to remove the embeded ad

--Twilio funcationality to answer the call and feed the audio
   

-- A Flask web-app that could be running at all times to provide the call content

### NOTE: Some of the flask code won't run on your machine but I'll show you what I did, and you can test it by making an audio call to (929) 209-6415

### IMPORT MODULES

In [2]:
#For the webscraping
from robobrowser import RoboBrowser

#This allows me to write a little application to run on my computer
from flask import Flask

#This is the twilio function to set up the voice call
from twilio.twiml.voice_response import VoiceResponse


### WEBSCRAPING TO FIND THE LATEST NPR NEWSCAST

In [3]:

#I had to hunt for a good page to find the newscasts.
#The main NPR page didn't work so I found a server for the podcast version

browser = RoboBrowser(history=True, parser ='html.parser')
browser.open('https://www.npr.org/podcasts/500005/npr-news-now')
     
#There are not obvious tags so I grab everything

links = browser.get_links()
newscast = []

# I use the folowing to search for audio links specifically

for link in links:
        if "mp3" in str(link):
            newscast.append(link.get("href"))
           
# This grabs the first, most recent audio file

latest = str(newscast[0])

print(latest)


https://play.podtrac.com/npr-500005/edge1.pod.npr.org/anon.npr-mp3/npr/newscasts/2019/10/21/newscast200805.mp3?siteplayer=true&size=4500000&awCollectionId=500005&awEpisodeId=772120172&dl=1


### The problem with this link is that it plays the podcast version of newscast, with ads and podcast promotion from the Podtrac company.  I don't want those things, so I strip out just the unique ID of the newscast and put it into a more direct link format I found.

In [4]:
new_url = "https://ondemand.npr.org/anon.npr-mp3/npr/newscasts" + latest[80:106] + ".mp3"
    
print(new_url)

https://ondemand.npr.org/anon.npr-mp3/npr/newscasts/2019/10/21/newscast200805.mp3


### I will want to have the time of the latest newscast for my announcement so I pull just that number from the unique ID and convert from military time

In [5]:
time_military = int(latest[100:102])

if (time_military) > 12:
    time = time_military - 12
else:
    time = time_military 
    
print(time,"o'clock")


8 o'clock


### FEED AUDIO FILE AND MESSAGE TO TWILIO

In [6]:
# This is the format that TWilio needs to answer calls:
def answer_call():
    
    # Start our TwiML response
    resp = VoiceResponse()
    
    # Read this message aloud to the caller (scroll -->)
    resp.say(f"This is Dial a Newscast, a Python programming project by Robert Smith. I'll grab the most recent NPR newscast from {time} o'clock. Standby.", voice='alice')
    
    # Play the mp3 of the newscast picked above
    resp.play(str(new_url))
    
    return str(resp)


Essentially this puts the message and the audio file into a format that Twilio can recognize like this "This is dial a newscast, a Python programming project by Robert Smith. I'll grab the most recent NPR newscast from 9 o'clock. Standby.https://ondemand.npr.org/anon.npr-mp3/npr/newscasts/2019/10/21/newscast210810.mp3"

### CREATE WEB-APP ON MY COMPUTER WITH FLASK

### Twilio needs a website with the above information in order to feed the audio. I learned how to create a Flask App to feed this function continuously to my local port http://localhost:5000/answer I tucked all of the code listed above into the web-app so it runs every time that port is accessed. NOTE: if you run this it won't work without the flask environment launched on your computer.

In [7]:
#Create default name for the app
app = Flask(__name__)
#Show the route to feed the information
@app.route("/answer", methods=['GET', 'POST'])

#ALL THE FOLLOWING CODE YOU HAVE ALREADY SEEN
def answer_call():
    
    browser.open('https://www.npr.org/podcasts/500005/npr-news-now')
    links = browser.find_all()
    newscast = []

    for link in links:
        test = str(link.get("href"))
        if "mp3" in test:
            newscast.append(link.get("href"))
        
    latest = str(newscast[0])
    new_url = "https://ondemand.npr.org/anon.npr-mp3/npr/newscasts" + latest[80:106] + ".mp3"
    time_military = int(latest[100:102])
    if (time_military) > 12:
        time = time_military -12
    else:
        time = time_military 

    # Start our TwiML response
    resp = VoiceResponse()
    # Read this message aloud to the caller
    resp.say(f"This is dial a newscast, a Python programming project by Robert Smith. I'll grab the most recent NPR newscast from {time} o'clock. Standby.", voice='alice')
    # Play the mp3 of the newscast above
    resp.play(str(new_url))
    return str(resp)

#This starts the app running
if __name__ == "__main__":
    app.run(debug=True)

 * Serving Flask app "__main__" (lazy loading)
 * Environment: production
   Use a production WSGI server instead.
 * Debug mode: on


OSError: [Errno 48] Address already in use

###  I used an app called ngrok to create an accessible url for my local port http://60597d49.ngrok.io/answer IF you click on that link, you'll see the updated output of the preceding code.

### I TESTED EVERYTHING WITH THE FOLLOWING CODE. IF YOU WANT IT TO CALL YOUR PHONE, PUT YOUR NUMBER IN THE "to = " SPOT

In [10]:

from twilio.rest import Client
account_sid = '...'
auth_token = '...'
client = Client(account_sid, auth_token)

call = client.calls.create(
                        url='http://60597d49.ngrok.io/answer',
                        to='...',
                        from_='+19292096415'
                    )

print(call.sid)

CA1f54e849838e7fec806f96d71f6636af


### In order to answer when called, I went to the Twilio page and put the ngrok url in the answer function. As long as my flask app is running, you can call 24 hours a day for the latest newscast. There is a delay in the posting of the newscast, so sometimes if it's 7:15 you'll still get the 6 o'clock newscast.  If you haven't tried yet, please call (929) 209-6415